# Instructions

1. Download the dataset and extract to get:
  
  * `annotations.json`
  * `train-image-url.csv`
  * `test-image-url.csv`

2. Upload the dataset files and `model.pt` trained model wieghts.

3. Run all cells before the training loop. Dataset creation via downloading images requires space and time. Run this segment (Training loop) to train the model on the data again. Connect to gpu runtime for faster processing. By default, model trains for only 50 epochs.

4. The inference loop has code to check performance metrics on validation data.

5. The inference loop also has code to generate results for the test set images and store it to the results list object. Each element of the results list is a Results object as defined by the ultralytics package.

# Installs

In [1]:
! pip install ultralytics

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 902.2/902.2 kB 16.2 MB/s eta 0:00:00


In [2]:
! git clone https://github.com/SnehilNair/JSON2YOLO

Cloning into 'JSON2YOLO'...
remote: Enumerating objects: 395, done.
remote: Counting objects: 100% (233/233), done.
remote: Compressing objects: 100% (65/65), done.
remote: Total 395 (delta 221), reused 168 (delta 168), pack-reused 162 (from 2)
Receiving objects: 100% (395/395), 113.12 KiB | 2.17 MiB/s, done.
Resolving deltas: 100% (242/242), done.


In [3]:
! cd JSON2YOLO && pip install -r requirements.txt

In [4]:
! mkdir customDataset

In [5]:
! rm -rd /content/CustomDataset

rm: cannot remove '/content/CustomDataset': No such file or directory


# Imports

In [175]:
from io import BytesIO
from PIL import Image, ImageDraw
import json
import requests
import matplotlib.pyplot as plt
import numpy as np
import os
import shutil
import pandas as pd
from sklearn.model_selection import train_test_split
import yaml
from ultralytics import YOLO
import random
import tqdm

# Processing

## 1. Convert annotations to txt labels

In [17]:
!cd JSON2YOLO && python general_json2yolo.py

Annotations /content/annotations.json: 100% 1500/1500 [00:01<00:00, 1425.67it/s]


In [18]:
label_files = os.listdir('/content/customDataset/labels/annotations')
len(label_files)

1500

## 2. Download Files (as per coco dataset structure)
```
.
└── root dir/
    ├── images/
    │   ├── train/
    │   │   └── (training images go here)
    │   └── val/
    │       └── (Validation images go here)
    └── labels/
        ├── train/
        │   └── (training labels go here)
        └── val/
            └── (validation labels go here)
```

In [19]:
json_path = r"/content/annotations.json"
data = None
with open(json_path, 'r') as file:
    data = json.load(file)

### Checks

In [20]:
data.keys()

dict_keys(['info', 'images', 'annotations', 'scene_annotations', 'licenses', 'categories', 'scene_categories'])

In [21]:
data['images'][0].keys()

dict_keys(['id', 'width', 'height', 'file_name', 'license', 'flickr_url', 'coco_url', 'date_captured', 'flickr_640_url'])

In [22]:
category_map = {i['id']: i['name'] for i in data['categories']}
category_map

{0: 'Aluminium foil',
 1: 'Battery',
 2: 'Aluminium blister pack',
 3: 'Carded blister pack',
 4: 'Other plastic bottle',
 5: 'Clear plastic bottle',
 6: 'Glass bottle',
 7: 'Plastic bottle cap',
 8: 'Metal bottle cap',
 9: 'Broken glass',
 10: 'Food Can',
 11: 'Aerosol',
 12: 'Drink can',
 13: 'Toilet tube',
 14: 'Other carton',
 15: 'Egg carton',
 16: 'Drink carton',
 17: 'Corrugated carton',
 18: 'Meal carton',
 19: 'Pizza box',
 20: 'Paper cup',
 21: 'Disposable plastic cup',
 22: 'Foam cup',
 23: 'Glass cup',
 24: 'Other plastic cup',
 25: 'Food waste',
 26: 'Glass jar',
 27: 'Plastic lid',
 28: 'Metal lid',
 29: 'Other plastic',
 30: 'Magazine paper',
 31: 'Tissues',
 32: 'Wrapping paper',
 33: 'Normal paper',
 34: 'Paper bag',
 35: 'Plastified paper bag',
 36: 'Plastic film',
 37: 'Six pack rings',
 38: 'Garbage bag',
 39: 'Other plastic wrapper',
 40: 'Single-use carrier bag',
 41: 'Polypropylene bag',
 42: 'Crisp packet',
 43: 'Spread tub',
 44: 'Tupperware',
 45: 'Disposable 

In [23]:
count = 0
for i in data['images']:
  filename = i['file_name']
  search = filename.replace("/", "_").split('.')[0] + ".txt"
  if search not in label_files:
    print(search)
    print(filename)
    print("NOT FOUND!")
    print("="*30)
    count += 1
  image_url = i['flickr_url']
  url = i['coco_url']

print(f"Number of files not found: {count}")

Number of files not found: 0


### Utility Functions

Make directory tree

In [24]:
! mkdir dataset dataset/images dataset/labels dataset/images/train dataset/images/val dataset/labels/train dataset/labels/val

In [25]:
def check_id_url_pair(url, id):
  assert data['images'][id]['flickr_url'] == url

In [26]:
train, test = pd.read_csv("/content/train-image-url.csv", header=None), pd.read_csv("/content/test-images-url.csv", header=None)
test.head()

0                                                  1
0  NaN  https://olm-s3.s3.eu-west-1.amazonaws.com/2019...
1  NaN  https://olm-s3.s3.eu-west-1.amazonaws.com/2019...
2  NaN  https://olm-s3.s3.eu-west-1.amazonaws.com/2019...
3  NaN  https://olm-s3.s3.eu-west-1.amazonaws.com/2019...
4  NaN  https://olm-s3.s3.eu-west-1.amazonaws.com/2019...

In [27]:
train.tail()

0                                                  1
1995  NaN  https://olm-s3.s3.eu-west-1.amazonaws.com/2019...
1996  NaN  https://olm-s3.s3.eu-west-1.amazonaws.com/2019...
1997  NaN  https://olm-s3.s3.eu-west-1.amazonaws.com/2019...
1998  NaN  https://olm-s3.s3.eu-west-1.amazonaws.com/2019...
1999  NaN  https://olm-s3.s3.eu-west-1.amazonaws.com/2019...

In [28]:
train.shape, test.shape

((2000, 2), (2618, 2))

In [29]:
train[1].head()

0    https://farm66.staticflickr.com/65535/33978196...
1    https://farm66.staticflickr.com/65535/47803331...
2    https://farm66.staticflickr.com/65535/40888872...
3    https://farm66.staticflickr.com/65535/47803331...
4    https://farm66.staticflickr.com/65535/33978199...
Name: 1, dtype: object

In [30]:
parsing_dict = {}
for i in data['images']:
  if train[1].eq(i['flickr_url']).any():
    parsing_dict[i['id']] = [i['file_name'], i['flickr_url']]

In [31]:
len(parsing_dict)

1438

In [32]:
parsing_dict

{0: ['batch_1/000006.jpg',
  'https://farm66.staticflickr.com/65535/33978196618_e30a59e0a8_o.png'],
 1: ['batch_1/000008.jpg',
  'https://farm66.staticflickr.com/65535/47803331152_ee00755a2e_o.png'],
 2: ['batch_1/000010.jpg',
  'https://farm66.staticflickr.com/65535/40888872753_08ffb24902_o.png'],
 3: ['batch_1/000019.jpg',
  'https://farm66.staticflickr.com/65535/47803331492_0e1085ca55_o.png'],
 4: ['batch_1/000026.jpg',
  'https://farm66.staticflickr.com/65535/33978199868_88ee160849_o.png'],
 5: ['batch_1/000047.jpg',
  'https://farm66.staticflickr.com/65535/33978200068_c6eed416ac_o.png'],
 6: ['batch_1/000055.jpg',
  'https://farm66.staticflickr.com/65535/47803332212_af8cfa9704_o.png'],
 7: ['batch_1/000001.jpg',
  'https://farm66.staticflickr.com/65535/33978202498_effbca58ef_o.png'],
 8: ['batch_1/000005.jpg',
  'https://farm66.staticflickr.com/65535/47803335992_9c58683430_o.png'],
 9: ['batch_1/000007.jpg',
  'https://farm66.staticflickr.com/65535/47855505601_f75a430abc_o.png'],


In [33]:
def downloader(url, name):
    res = requests.get(url, stream=True)
    if res.status_code != 200:
        raise "Url Not Found!"
    return Image.open(BytesIO(res.content)).convert("RGB")

## Making train test split

In [34]:
parsing_pd = pd.DataFrame.from_dict(parsing_dict, orient='index')
parsing_pd.head()

0                                                  1
0  batch_1/000006.jpg  https://farm66.staticflickr.com/65535/33978196...
1  batch_1/000008.jpg  https://farm66.staticflickr.com/65535/47803331...
2  batch_1/000010.jpg  https://farm66.staticflickr.com/65535/40888872...
3  batch_1/000019.jpg  https://farm66.staticflickr.com/65535/47803331...
4  batch_1/000026.jpg  https://farm66.staticflickr.com/65535/33978199...

In [35]:
parsing_pd.shape

(1438, 2)

In [36]:
train, val = train_test_split(parsing_pd, test_size=0.1, random_state=42)
train.shape

(1294, 2)

In [37]:
val.shape

(144, 2)

## Populating Directories

In [38]:
train[1].iloc[0]

'https://olm-s3.s3.eu-west-1.amazonaws.com/2018/08/28/zGSwGdiiq3gIybROf1HU71pBu6ry2VftipIDjzlO.jpeg'

In [39]:
val[1].eq("https://farm66.staticflickr.com/65535/33978196618_e30a59e0a8_o.png").any()

False

In [40]:
path = "/content/dataset"
for idx, item in parsing_dict.items():
  # print(idx, item)
  name = item[0].replace("/", "_")
  label = name.split('.')[0] + '.txt'
  url = item[1]
  # print(name, label, url)
  # break

  # Check if there is an annotation for the image file
  if label not in os.listdir('/content/customDataset/labels/annotations'):
    print(f"Label not found: {label}")
    break

  # Check if image belongs to train set
  if train[1].eq(url).any():
    a = downloader(url, name)
    a.save(os.path.join(path, 'images', 'train', name.split('.')[0]+'.jpg'))
    shutil.copy(os.path.join('/content/customDataset/labels/annotations', label), os.path.join(path, 'labels', 'train', label))

  # Check if image belongs to validate set otherwise
  else:
    # print(val[1].eq(url).any())
    if val[1].eq(url).any() == False: print(f"Error with file: {url}")
    a = downloader(url, name)
    a.save(os.path.join(path, 'images', 'val', name.split('.')[0]+'.jpg'))
    shutil.copy(os.path.join('/content/customDataset/labels/annotations', label), os.path.join(path, 'labels', 'val', label))


True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True


## Make yaml file

Yaml file structure :

```
path: ../datasets/coco8-seg # dataset root dir
train: images/train # train images (relative to 'path') 4 images
val: images/val # val images (relative to 'path') 4 images
test: # test images (optional)

# Classes
names:
  0: person
  1: bicycle
  2: car
  3: motorcycle
  ...
  76: scissors
  77: teddy bear
  78: hair drier
  79: toothbrush
```

In [41]:
yaml_struc = {
    "path": "/content/dataset",
    "train": "images/train",
    "val": "images/val",
    "names": category_map
}

yaml_struc

{'path': '/content/dataset',
 'train': 'images/train',
 'val': 'images/val',
 'names': {0: 'Aluminium foil',
  1: 'Battery',
  2: 'Aluminium blister pack',
  3: 'Carded blister pack',
  4: 'Other plastic bottle',
  5: 'Clear plastic bottle',
  6: 'Glass bottle',
  7: 'Plastic bottle cap',
  8: 'Metal bottle cap',
  9: 'Broken glass',
  10: 'Food Can',
  11: 'Aerosol',
  12: 'Drink can',
  13: 'Toilet tube',
  14: 'Other carton',
  15: 'Egg carton',
  16: 'Drink carton',
  17: 'Corrugated carton',
  18: 'Meal carton',
  19: 'Pizza box',
  20: 'Paper cup',
  21: 'Disposable plastic cup',
  22: 'Foam cup',
  23: 'Glass cup',
  24: 'Other plastic cup',
  25: 'Food waste',
  26: 'Glass jar',
  27: 'Plastic lid',
  28: 'Metal lid',
  29: 'Other plastic',
  30: 'Magazine paper',
  31: 'Tissues',
  32: 'Wrapping paper',
  33: 'Normal paper',
  34: 'Paper bag',
  35: 'Plastified paper bag',
  36: 'Plastic film',
  37: 'Six pack rings',
  38: 'Garbage bag',
  39: 'Other plastic wrapper',
  40: '

In [42]:
with open("/content/dataset/options.yaml", "w") as file:
  yaml.dump(yaml_struc, file, sort_keys=False)

# Training Loop

In [ ]:
# model = YOLO("yolo11n-seg.pt")
model = YOLO("/content/model.pt")

In [ ]:
results = model.train(data="/content/dataset/options.yaml", epochs=50, imgsz=640)

Ultralytics 8.3.52 🚀 Python-3.10.12 torch-2.5.1+cu121 CUDA:0 (Tesla T4, 15102MiB)
engine/trainer: task=segment, mode=train, model=/content/best_5.pt, data=/content/dataset/options.yaml, epochs=50, time=None, patience=100, batch=16, imgsz=640, save=True, save_period=-1, cache=False, device=None, workers=8, project=None, name=train, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=False, agnostic_nms=False, classes=None, retina_masks=False, embed=None, show=False, save_frames=False, save_txt=False, save_conf=False, save_crop=False, show_labels=True, show_conf=True

100%|██████████| 755k/755k [00:00<00:00, 28.4MB/s]



                   from  n    params  module                                       arguments                     
  0                  -1  1       464  ultralytics.nn.modules.conv.Conv             [3, 16, 3, 2]                 
  1                  -1  1      4672  ultralytics.nn.modules.conv.Conv             [16, 32, 3, 2]                
  2                  -1  1      6640  ultralytics.nn.modules.block.C3k2            [32, 64, 1, False, 0.25]      
  3                  -1  1     36992  ultralytics.nn.modules.conv.Conv             [64, 64, 3, 2]                
  4                  -1  1     26080  ultralytics.nn.modules.block.C3k2            [64, 128, 1, False, 0.25]     
  5                  -1  1    147712  ultralytics.nn.modules.conv.Conv             [128, 128, 3, 2]              
  6                  -1  1     87040  ultralytics.nn.modules.block.C3k2            [128, 128, 1, True]           
  7                  -1  1    295424  ultralytics.nn.modules.conv.Conv             [128

100%|██████████| 5.35M/5.35M [00:00<00:00, 101MB/s]


AMP: checks passed ✅


...

                   all        144        440      0.522       0.19      0.229      0.198      0.522       0.19      0.222      0.178

      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


      36/50      3.56G     0.9049      1.735      1.598     0.9573         51        640: 100%|██████████| 81/81 [01:37<00:00,  1.20s/it]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 5/5 [00:04<00:00,  1.21it/s]


                   all        144        440      0.568      0.184      0.239      0.207      0.568      0.184      0.237      0.189

      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


      37/50      3.19G     0.8926       1.79       1.56     0.9428        102        640:   4%|▎         | 3/81 [00:03<01:19,  1.01s/it]


KeyboardInterrupt: 

In [ ]:
import torch
import ultralytics
print(torch.__version__)
print(ultralytics.__version__)

2.5.1+cu121
8.3.51


In [ ]:
model.export()

TypeError: 'IterableSimpleNamespace' object is not subscriptable

# Inference Loop

## Preamble

In [43]:
model = YOLO("/content/model.pt")

In [44]:
test = pd.read_csv("/content/test-images-url.csv", header=None)

## Performance Metrics

In [45]:
metrics = model.val()

Ultralytics 8.3.53 🚀 Python-3.10.12 torch-2.5.1+cu121 CPU (Intel Xeon 2.20GHz)
YOLO11n-seg summary (fused): 265 layers, 2,846,268 parameters, 0 gradients, 10.3 GFLOPs


100%|██████████| 755k/755k [00:00<00:00, 15.6MB/s]
val: Scanning /content/dataset/labels/val... 144 images, 0 backgrounds, 0 corrupt: 100%|██████████| 144/144 [00:00<00:00, 456.62it/s]

val: New cache created: /content/dataset/labels/val.cache



                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 9/9 [01:08<00:00,  7.65s/it]


                   all        144        440       0.62       0.18      0.259      0.223       0.62       0.18      0.245      0.194
        Aluminium foil          4          5      0.509        0.2      0.204      0.202      0.509        0.2      0.204       0.18
  Other plastic bottle          4          6      0.781      0.833      0.857      0.686      0.781      0.833      0.857      0.669
  Clear plastic bottle         18         21      0.401      0.286      0.387      0.316      0.401      0.286      0.387      0.278
          Glass bottle          8         11       0.45     0.0818      0.142     0.0849       0.45     0.0818      0.145     0.0784
    Plastic bottle cap         15         16      0.608      0.292       0.34      0.246      0.608      0.292      0.299      0.158
      Metal bottle cap          1          1          1          0     0.0474     0.0426          1          0     0.0474     0.0354
          Broken glass          4         56          1          0   

In [112]:
metrics.fitness

0.42597103494301114

In [83]:
cap = ["B_Precision", "B_Recall", "B_mAP50", "B_mAP50-95", "M_Precision", "M_Recall", "M_mAP50", "M_mAP50-95"]
for idx, i in enumerate(metrics.mean_results()):
  print(f"{cap[idx]}: {np.round(i, 3)}")

B_Precision: 0.62
B_Recall: 0.18
B_mAP50: 0.259
B_mAP50-95: 0.223
M_Precision: 0.62
M_Recall: 0.18
M_mAP50: 0.245
M_mAP50-95: 0.194


### Generate IoU scores

In [171]:
metric_data = {}

for i in data['annotations']:
  if i['image_id'] in metric_data.keys():
    metric_data[i['image_id']][i['category_id']] = i['bbox']
  else:
    metric_data[i['image_id']] = {}
    metric_data[i['image_id']][i['category_id']] = i['bbox']
    count += 1

len(metric_data)

1500

In [119]:
image_id_map = {}
for i in data['images']:
  image_id_map[i['id']] = i['flickr_url']
len(image_id_map)

1500

In [164]:
def iou(boxp, boxgt):
  """
  Get IoU scores given Prediction box and Ground Truth Box in xyxy format.
  boxp: [x1, y1, x2, y2]
  boxgt: [x1, y1, x2, y2]
  """
  x1 = max(boxp[0], boxgt[0])
  y1 = max(boxp[1], boxgt[1])
  x2 = min(boxp[2], boxgt[2])
  y2 = min(boxp[3], boxgt[3])
  intersection = max(0, x2 - x1) * max(0, y2 - y1)
  area1 = (boxp[2] - boxp[0]) * (boxp[3] - boxp[1])
  area2 = abs(boxgt[2] - boxgt[0]) * abs(boxgt[3] - boxgt[1])
  union = area1 + area2 - intersection
  return intersection / union

In [165]:
def xywh_to_xyxy(box):
    """
    Convert a bounding box from xywh format to xyxy format.
    xywh format: [center_x, center_y, width, height]
    xyxy format: [x_min, y_min, x_max, y_max]
    """
    x, y, w, h = box
    x_min = x - w / 2
    y_min = y - h / 2
    x_max = x + w / 2
    y_max = y + h / 2
    return [x_min, y_min, x_max, y_max]

In [177]:
iou_scores = []
historical = []
for epoch in tqdm.tqdm(range(1, 100)):
  s = random.sample(metric_data.keys(), 100)
  for i in s:
    a = model.predict(image_id_map[i])[0].boxes
    b = metric_data[i]
    for idx, i in enumerate(a.cls):
      # print(idx, i)
      if int(i.item()) in b.keys():
        # print(b[i.item()])
        iou_scores.append(iou(a.xyxy[idx], xywh_to_xyxy(b[i.item()])))
  v = (sum(iou_scores)/len(iou_scores)).item()
  historical.append(v)

  0%|          | 0/99 [00:00<?, ?it/s]

<ipython-input-177-4cce3bdd8d10>:4: DeprecationWarning: Sampling from a set deprecated
since Python 3.9 and will be removed in a subsequent version.
  s = random.sample(metric_data.keys(), 100)

1.88MB [00:00, 26.0MB/s]


image 1/1 /content/48693695908_0101b57186_o.png: 640x320 3 Corrugated cartons, 168.6ms
Speed: 3.0ms preprocess, 168.6ms inference, 12.2ms postprocess per image at shape (1, 3, 640, 320)




1.22MB [00:00, 18.8MB/s]


image 1/1 /content/47066800644_6d005deb0a_o.png: 640x480 6 Aluminium foils, 1 Paper bag, 215.3ms
Speed: 3.4ms preprocess, 215.3ms inference, 20.6ms postprocess per image at shape (1, 3, 640, 480)



...

 98%|█████████▊| 97/99 [1:38:24<01:39, 49.74s/it]


Found https://farm66.staticflickr.com/65535/40889467093_5de26e20dd_o.png locally at 40889467093_5de26e20dd_o.png
image 1/1 /content/40889467093_5de26e20dd_o.png: 480x640 1 Other plastic, 350.9ms
Speed: 6.3ms preprocess, 350.9ms inference, 7.1ms postprocess per image at shape (1, 3, 480, 640)

Found https://farm66.staticflickr.com/65535/48701320137_bfd555a59b_o.png locally at 48701320137_bfd555a59b_o.png
image 1/1 /content/48701320137_bfd555a59b_o.png: 640x320 1 Plastic lid, 302.3ms
Speed: 3.9ms preprocess, 302.3ms inference, 5.1ms postprocess per image at shape (1, 3, 640, 320)

Found https://olm-s3.s3.eu-west-1.amazonaws.com/2019/04/18/bY2Tazdw3BSAbnoo53PWCH8xF76z8K1vC9uc0tuu.jpeg locally at bY2Tazdw3BSAbnoo53PWCH8xF76z8K1vC9uc0tuu.jpeg
image 1/1 /content/bY2Tazdw3BSAbnoo53PWCH8xF76z8K1vC9uc0tuu.jpeg: 480x640 (no detections), 346.8ms
Speed: 5.9ms preprocess, 346.8ms inference, 0.9ms postprocess per image at shape (1, 3, 480, 640)

Found https://olm-s3.s3.eu-west-1.amazonaws.com/2019/

 99%|█████████▉| 98/99 [1:39:12<00:49, 49.24s/it]


Found https://farm66.staticflickr.com/65535/48661146411_80fb7e453a_o.png locally at 48661146411_80fb7e453a_o.png
image 1/1 /content/48661146411_80fb7e453a_o.png: 640x480 1 Plastic film, 1 Unlabeled litter, 310.6ms
Speed: 5.5ms preprocess, 310.6ms inference, 11.2ms postprocess per image at shape (1, 3, 640, 480)

Found https://farm66.staticflickr.com/65535/47856319211_dc3a523be8_o.png locally at 47856319211_dc3a523be8_o.png
image 1/1 /content/47856319211_dc3a523be8_o.png: 480x640 1 Drink can, 323.9ms
Speed: 5.2ms preprocess, 323.9ms inference, 6.8ms postprocess per image at shape (1, 3, 480, 640)

Found https://farm66.staticflickr.com/65535/47803621202_9819ba551e_o.png locally at 47803621202_9819ba551e_o.png
image 1/1 /content/47803621202_9819ba551e_o.png: 640x480 1 Spread tub, 321.7ms
Speed: 5.3ms preprocess, 321.7ms inference, 6.5ms postprocess per image at shape (1, 3, 640, 480)

Found https://farm66.staticflickr.com/65535/48694282352_424aa2ca6a_o.png locally at 48694282352_424aa2ca

100%|██████████| 99/99 [1:40:00<00:00, 60.61s/it]


In [178]:
print(min(historical), max(historical))

0.07821481674909592 0.1025274395942688


### Download  Validation metrics as zip

In [62]:
import shutil
import os

def zip_folder(folder_path, output_path):
    shutil.make_archive(output_path, 'zip', folder_path)

# Assuming metrics are stored in a folder named 'val' within the current directory
zip_folder('/content/runs/segment/val', '/content/val_metrics')

from google.colab import files
files.download('/content/val_metrics.zip')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

## Inference on Test set Data

In [65]:
results = []
for i in test.iterrows():
  url = i[1][1]
  img = downloader(url, "/content/Test1.jpg")
  a = model(img)
  results.append(a[0])


0: 480x640 1 Plastic lid, 250.7ms
Speed: 4.4ms preprocess, 250.7ms inference, 14.5ms postprocess per image at shape (1, 3, 480, 640)


## Inference on custom image

In [ ]:
url = "" # @param {"type":"string","placeholder":"\"https://url_to_image"}

In [ ]:
result = model(url)

# Rough Testing

In [ ]:
path = "/content/customDataset/images"
for i in data['images']:
  id = i['id']
  filename = i['file_name']
  search = filename.replace("/", "_").split('.')[0] + ".txt"
  if search not in label_files:
    print(f"{filename} : {search} Not Found!")
    break
  name = filename.replace("/", "_").split('.')[0] + '.jpg'
  url = i['flickr_url']
  print(f"{id}. Processing: {filename} @ {url}")
  if os.path.join(path, name) not in os.listdir(path): downloader(url, name, path)

0. Processing: batch_1/000006.jpg @ https://farm66.staticflickr.com/65535/33978196618_e30a59e0a8_o.png
1. Processing: batch_1/000008.jpg @ https://farm66.staticflickr.com/65535/47803331152_ee00755a2e_o.png
2. Processing: batch_1/000010.jpg @ https://farm66.staticflickr.com/65535/40888872753_08ffb24902_o.png
3. Processing: batch_1/000019.jpg @ https://farm66.staticflickr.com/65535/47803331492_0e1085ca55_o.png
4. Processing: batch_1/000026.jpg @ https://farm66.staticflickr.com/65535/33978199868_88ee160849_o.png
5. Processing: batch_1/000047.jpg @ https://farm66.staticflickr.com/65535/33978200068_c6eed416ac_o.png
6. Processing: batch_1/000055.jpg @ https://farm66.staticflickr.com/65535/47803332212_af8cfa9704_o.png
7. Processing: batch_1/000001.jpg @ https://farm66.staticflickr.com/65535/33978202498_effbca58ef_o.png
8. Processing: batch_1/000005.jpg @ https://farm66.staticflickr.com/65535/47803335992_9c58683430_o.png
9. Processing: batch_1/000007.jpg @ https://farm66.staticflickr.com/65535

In [ ]:
! rm -r /content/customDataset/images/*

In [ ]:

shutil.make_archive("/content/customDataset", 'zip', "/content/customDataset")

'/content/customDataset.zip'